In [2]:
import os
os.system('nvidia-smi')
# 주의! 파인튜닝에는 GPU가 필요해요! 

Fri Mar  1 23:09:32 2024       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.239.06   Driver Version: 551.23       CUDA Version: 12.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ...  On   | 00000000:09:00.0  On |                  N/A |
|  0%   36C    P8    19W / 180W |   1690MiB / 12288MiB |     18%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

0

In [3]:
import torch
print(torch.cuda.is_available())

True


In [4]:
# dataset download
import os
# runtime env change
os.chdir('/home/layla/learning-ai/data')

from torchtext.datasets import IMDB

train_iter = IMDB(split='train')
test_iter = IMDB(split='test')


In [5]:
print(train_iter)

ShardingFilterIterDataPipe


In [6]:
import random
train = list(train_iter)
test = list(test_iter)

train_sample = random.sample(train, 1000)
test_sample = random.sample(test, 1000)

print(train_sample[0])
print(test_sample[0])

(1, "Don't even waste your time, let alone pay rental for this piece of dreck! How it got made is beyond me. (I don't know why there's a minimum of 10 lines... I've already summarized this trashy movie, but, oh well...) The acting was awful, like they all needed lessons. The plot was weak, the ending... Feh! I think the cinematography was the only thing that didn't totally suck... well, maybe the sound was minimalistically OK. The one good thing is, if they could make this movie, even make some money with it, there may be hope for any screenwriter with a REAL idea. So, you-all take heart! I guess the same holds true of actors... if these people actually got paid, then you can, too!")
(2, "If this film doesn't at least be selected for an oscar nominee for best foreign film I'm going to stop waking at nights watching the event. Fridrik Thor Fridriksson has proven that money isn't the key to making a good movie but originality. Out of a cold country comes a warm but thought-provoking film

In [7]:
train_text = []
train_labels = []
test_text = []
test_labels = []

for label,text in train_sample:
    train_labels.append(1 if label == 2 else 0)
    train_text.append(text)
    
for label,text in test_sample:
    test_labels.append(1 if label == 2 else 0)
    test_text.append(text)

print(train_text[:10])

["Don't even waste your time, let alone pay rental for this piece of dreck! How it got made is beyond me. (I don't know why there's a minimum of 10 lines... I've already summarized this trashy movie, but, oh well...) The acting was awful, like they all needed lessons. The plot was weak, the ending... Feh! I think the cinematography was the only thing that didn't totally suck... well, maybe the sound was minimalistically OK. The one good thing is, if they could make this movie, even make some money with it, there may be hope for any screenwriter with a REAL idea. So, you-all take heart! I guess the same holds true of actors... if these people actually got paid, then you can, too!", 'Fox\'s "The True Story Of Jesse James" (1957) is a remarkably poor widescreen remake of their prestigious 1939 Tyrone Power/Henry Fonda classic "Jesse James". I\'m not sure where the fault lies but the casting in this version of the two central characters, the uneven direction of Nicholas Ray and the ham-fis

In [8]:
print(train_labels[:10])

[0, 0, 0, 1, 0, 1, 0, 1, 0, 1]


In [9]:
from sklearn.model_selection import train_test_split
# 데이터셋 분할

train_text, valid_text, train_labels, valid_labels = train_test_split(train_text, train_labels, test_size=0.2, random_state=7)
print(len(train_text), len(valid_text), len(test_text))

800 200 1000


In [9]:
train_text[:10]

['So what constitutes a real independent film? In a day and age where the latest fad of mainstream hollywood is to appear rugged and cutting edge, I\'m sorry to say that what the general public tends to perceive as independent film is usually nothing more than a clever marketing ploy.<br /><br />Which is why we should be glad that films like "Hatred of a Minute" exist. Across the board, this film makes a point out of contradicting its own template (indie horror film). Love it or hate it, "Hatred" isn\'t afraid of being what it is, and in watching this film, you get the real sense that Kallio (the director) didn\'t just make this film to spray fake blood all over the place, he\'s in this to tell stories. Good ones. You may find this film in the horror film section of your video store, but don\'t be fooled, this story is also about love, about good people pushed over the edge, and that oh-so-distant light at the end of the tunnel.<br /><br />If you expect smut, or an Evil Dead ripoff, st

In [20]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')


In [21]:
train_encodings = tokenizer(train_text, truncation=True, padding=True)
valid_encodings = tokenizer(valid_text, truncation=True, padding=True)
test_encodings = tokenizer(test_text, truncation=True, padding=True)

print(train_encodings)

{'input_ids': [[101, 1996, 2269, 1997, 1996, 2040, 1005, 1055, 14813, 7101, 1010, 6766, 4231, 1010, 2001, 2315, 4300, 1012, 1045, 2179, 2061, 2116, 12319, 2090, 12648, 5405, 1998, 6766, 4231, 1999, 2023, 3185, 1012, 20503, 3067, 6894, 1010, 2040, 2788, 2058, 18908, 2015, 1010, 2106, 3243, 1037, 2204, 3105, 1999, 2023, 2028, 1010, 1998, 2001, 2583, 2000, 2735, 5048, 2006, 12648, 5405, 1999, 2296, 2735, 1012, 2748, 1010, 1045, 5993, 1010, 2909, 2198, 10312, 7078, 2296, 3496, 1012, 2009, 2001, 1037, 2200, 1000, 2367, 1000, 3185, 1010, 12067, 1996, 13972, 2000, 2031, 1037, 12185, 2046, 2178, 2166, 1012, 2057, 2411, 3046, 2000, 4608, 1037, 2128, 15532, 1997, 2023, 3185, 2006, 5871, 1012, 2643, 2717, 12648, 5405, 1025, 2023, 2001, 2107, 2019, 22249, 3185, 1012, 2172, 18312, 1998, 16784, 2091, 2000, 1996, 4138, 1998, 1055, 25083, 3762, 1013, 22666, 1012, 1996, 2485, 6860, 2090, 5405, 1998, 2909, 2198, 2003, 2738, 2203, 27242, 1012, 102, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [22]:
print(train_encodings['input_ids'][0])

[101, 1996, 2269, 1997, 1996, 2040, 1005, 1055, 14813, 7101, 1010, 6766, 4231, 1010, 2001, 2315, 4300, 1012, 1045, 2179, 2061, 2116, 12319, 2090, 12648, 5405, 1998, 6766, 4231, 1999, 2023, 3185, 1012, 20503, 3067, 6894, 1010, 2040, 2788, 2058, 18908, 2015, 1010, 2106, 3243, 1037, 2204, 3105, 1999, 2023, 2028, 1010, 1998, 2001, 2583, 2000, 2735, 5048, 2006, 12648, 5405, 1999, 2296, 2735, 1012, 2748, 1010, 1045, 5993, 1010, 2909, 2198, 10312, 7078, 2296, 3496, 1012, 2009, 2001, 1037, 2200, 1000, 2367, 1000, 3185, 1010, 12067, 1996, 13972, 2000, 2031, 1037, 12185, 2046, 2178, 2166, 1012, 2057, 2411, 3046, 2000, 4608, 1037, 2128, 15532, 1997, 2023, 3185, 2006, 5871, 1012, 2643, 2717, 12648, 5405, 1025, 2023, 2001, 2107, 2019, 22249, 3185, 1012, 2172, 18312, 1998, 16784, 2091, 2000, 1996, 4138, 1998, 1055, 25083, 3762, 1013, 22666, 1012, 1996, 2485, 6860, 2090, 5405, 1998, 2909, 2198, 2003, 2738, 2203, 27242, 1012, 102, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [23]:
print(tokenizer.decode(train_encodings['input_ids'][0]))

[CLS] the father of the who's alcoholic drummer, keith moon, was named arthur. i found so many similarities between dudley moore and keith moon in this movie. liza minelli, who usually overacts, did quite a good job in this one, and was able to turn cheek on dudley moore in every turn. yes, i agree, sir john stole absolutely every scene. it was a very " different " movie, enabling the viewer to have a glimpse into another life. we often try to catch a rerun of this movie on satellite. god rest dudley moore ; this was such an enjoyable movie. much satire and thumbs down to the rich and snobby / affluent. the close friendship between moore and sir john is rather endearing. [SEP] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [P

In [24]:
class IMDbDataset(torch.utils.data.Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels

    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        item['labels'] = torch.tensor(self.labels[idx])
        return item

    def __len__(self):
        return len(self.labels)

In [25]:
train_dataset = IMDbDataset(train_encodings, train_labels)
valid_dataset = IMDbDataset(valid_encodings, valid_labels)
test_dataset = IMDbDataset(test_encodings, test_labels)

In [27]:
print(train_dataset[0])

{'input_ids': tensor([  101,  1996,  2269,  1997,  1996,  2040,  1005,  1055, 14813,  7101,
         1010,  6766,  4231,  1010,  2001,  2315,  4300,  1012,  1045,  2179,
         2061,  2116, 12319,  2090, 12648,  5405,  1998,  6766,  4231,  1999,
         2023,  3185,  1012, 20503,  3067,  6894,  1010,  2040,  2788,  2058,
        18908,  2015,  1010,  2106,  3243,  1037,  2204,  3105,  1999,  2023,
         2028,  1010,  1998,  2001,  2583,  2000,  2735,  5048,  2006, 12648,
         5405,  1999,  2296,  2735,  1012,  2748,  1010,  1045,  5993,  1010,
         2909,  2198, 10312,  7078,  2296,  3496,  1012,  2009,  2001,  1037,
         2200,  1000,  2367,  1000,  3185,  1010, 12067,  1996, 13972,  2000,
         2031,  1037, 12185,  2046,  2178,  2166,  1012,  2057,  2411,  3046,
         2000,  4608,  1037,  2128, 15532,  1997,  2023,  3185,  2006,  5871,
         1012,  2643,  2717, 12648,  5405,  1025,  2023,  2001,  2107,  2019,
        22249,  3185,  1012,  2172, 18312,  1998, 

In [28]:
from transformers import BertForSequenceClassification

model = BertForSequenceClassification.from_pretrained('bert-base-uncased')

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [29]:
print(model)

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

In [30]:
from transformers import Trainer, TrainingArguments

training_args = TrainingArguments(
    output_dir='./bert/output',
    num_train_epochs=30,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=64,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./bert/logs',
    logging_steps=10,
)

In [31]:
print(training_args)

TrainingArguments(
_n_gpu=1,
accelerator_config={'split_batches': False, 'dispatch_batches': None, 'even_batches': True, 'use_seedable_sampler': True},
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_persistent_workers=False,
dataloader_pin_memory=True,
dataloader_prefetch_factor=None,
ddp_backend=None,
ddp_broadcast_buffers=None,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=False,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_steps=None,
evaluation_strategy=no,
fp16=False,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
fsdp=[],
fsdp_config={'min_num_params': 0, 'xla': False, 'xla_fsdp_v2': False, 'xla_fsdp_grad_ckpt': False},
fsdp_min_num_params=0,
fsdp_transformer_la

In [32]:
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
model = model.to(device)

In [34]:
print(device)

cuda


In [35]:
input_tokens = tokenizer(['i love you furina', 'layla is so cute, maybe like a cat', 'if i was a professor, maybe i can see layla on real life', 'Do you merry me, focalors?'], return_tensors='pt', padding=True, truncation=True)

outputs = model(torch.tensor(input_tokens['input_ids']).to(device))

/tmp/ipykernel_25131/2771625415.py:3: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  outputs = model(torch.tensor(input_tokens['input_ids']).to(device))
We strongly recommend passing in an `attention_mask` since your input_ids may be padded. See https://huggingface.co/docs/transformers/troubleshooting#incorrect-output-when-padding-tokens-arent-masked.


In [37]:
label_dict = {1: 'negative', 0: 'positive'}

print([label_dict[i] for i in torch.argmax(outputs.logits, axis=1).cpu().numpy()])

['positive', 'positive', 'positive', 'positive']


In [39]:
from transformers import Trainer

In [40]:
trainer = Trainer(
    model = model,
    args = training_args,
    train_dataset = train_dataset,
    eval_dataset = valid_dataset
)

trainer.train()

TrainOutput(global_step=1500, training_loss=0.07732433580073605, metrics={'train_runtime': 9273.7211, 'train_samples_per_second': 2.588, 'train_steps_per_second': 0.162, 'total_flos': 6314665328640000.0, 'train_loss': 0.07732433580073605, 'epoch': 30.0})

In [41]:
input_tokens = tokenizer(['i love you furina', 'layla is so cute, maybe like a cat', 'if i was a professor, maybe i can see layla on real life', 'Do you merry me, focalors?'], return_tensors='pt', padding=True, truncation=True)

outputs = model(torch.tensor(input_tokens['input_ids']).to(device))

label_dict = {1: 'negative', 0: 'positive'}

print([label_dict[i] for i in torch.argmax(outputs.logits, axis=1).cpu().numpy()])

['negative', 'negative', 'negative', 'negative']


/tmp/ipykernel_25131/2256801497.py:3: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  outputs = model(torch.tensor(input_tokens['input_ids']).to(device))
